<a href="https://colab.research.google.com/github/salonieerego/Yorktown/blob/main/BB_Geocoding.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [12]:
#READ IN DATA

from google.colab import auth
auth.authenticate_user()

import gspread
from google.auth import default
creds, _ = default()

gc = gspread.authorize(creds)

worksheet = gc.open('BB Geocoding').sheet1

# get_all_values gives a list of rows.
rows = worksheet.get_all_values()

# Convert to a DataFrame and render.
import pandas as pd
bb = pd.DataFrame.from_records(rows)
bb.columns = bb.iloc[0]
bb = bb[1:]


In [13]:

bb.head()


0             Restaurant                   Where? Borough  \
1  Melanies Roti & Grill              Castle Hill   Bronx   
2        Juices for Life  Castle Hill / E Tremont   Bronx   
3      Jenny's Roti Shop              Castle Hill   Bronx   
4               Juiceade        Claremont Village   Bronx   
5      Jimmy's On the Go               Morrisania   Bronx   

0                                            Address            Service  \
1                              1248 Castle Hill Road  pickup + delivery   
2  1026 Castle Hill Ave & 3463 E Tremont Ave, The...             Pickup   
3          1262 Castle Hill Ave, The Bronx, NY 10462  pickup + delivery   
4    1345 Southern Blvd Store 1, The Bronx, NY 10459  pickup + delivery   
5                536 E 168th St, The Bronx, NY 10456             pickup   

0           Phone                                            Website Merch  \
1  (718) 409-1088  http://www.melaniesrotigrillrestaurant.com/ind...         
2  (347) 281-9844                          http://juicesforlife.nyc/         
3  (347) 281-8558  https://www.facebook.com/Jennys-Roti-Shop-1192...         
4  (718) 991-6369                          https://www.juiceade.com/         
5  (718) 842-2324                                                            

0 Gift cards Other  
1                   
2                   
3                   
4                   
5

In [14]:
from pyasn1.type.univ import Null
from geopy.geocoders import Nominatim
import pprint

geolocator = Nominatim(user_agent="bb")
lat_count = 0
long_count = 0
non_geocodable = []
geocodable = []

#Create null dicts - to be populated with lats/longs from geocode
for index,row in bb.iterrows():
    geocodable.append({'Address':row['Address'],'latitude':Null,'longitude':Null})

#Geocoded Addresses added to geocodable, non-geocodable addresses => non_geocodable
for add in geocodable:
  try:
    add['latitude']=geolocator.geocode(add['Address']).latitude
  except:
    lat_count = lat_count+1
    non_geocodable.append(add['Address'])
  try:
    add['longitude']=geolocator.geocode(add['Address']).longitude
  except:
    long_count = long_count+1
    if add['Address'] not in non_geocodable:
      non_geocodable.append(add['Address'])


  


In [15]:
#Remove Nulls from geocodable
final_geocodable = []
for add in geocodable:
  if isinstance(add['latitude'],float):
    final_geocodable.append(add)

#Convert lats and longs back to a df, and merge back to main df
geo_df = pd.DataFrame(final_geocodable)
final_bb = bb.merge(geo_df,left_on='Address',right_on='Address')



In [16]:
#Rename a few columns
final_bb = final_bb.rename(columns={'Where?':'Neighborhood','Gift cards':'Gift_Cards'})
final_bb.head()

Restaurant Neighborhood Borough  \
0  Melanies Roti & Grill  Castle Hill   Bronx   
1      Jenny's Roti Shop  Castle Hill   Bronx   
2      Jimmy's On the Go   Morrisania   Bronx   
3  Corner Style Jamaican    Concourse   Bronx   
4         Sam's Soulfood    Concourse   Bronx   

                                     Address            Service  \
0                      1248 Castle Hill Road  pickup + delivery   
1  1262 Castle Hill Ave, The Bronx, NY 10462  pickup + delivery   
2        536 E 168th St, The Bronx, NY 10456             pickup   
3       1195 Walton Ave, The Bronx, NY 10452  pickup + delivery   
4         598 Grand Concourse, The Bronx, NY  pickup + delivery   

            Phone                                            Website Merch  \
0  (718) 409-1088  http://www.melaniesrotigrillrestaurant.com/ind...         
1  (347) 281-8558  https://www.facebook.com/Jennys-Roti-Shop-1192...         
2  (718) 842-2324                                                            
3  (718) 410-8460                                                            
4    718-665-1409                       http://www.samssoulfood.com/         

  Gift_Cards Other   latitude   longitude  
0                  -33.730982  151.017816  
1                   40.833790  -73.851306  
2                   40.830633  -73.905308  
3                   40.834929  -73.919671  
4                   40.819740  -73.926324

In [17]:
!pip install geopandas
#Manually installing geopandas since it's missing otherwise

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [18]:
#Geoplotting
from shapely.geometry import Point, LineString
import geopandas as gpd
import matplotlib.pyplot as plt

#Add geom - ATTEMPT AT ADDING POINTS
final_bb['geometry'] = Null
geometry = [Point(xy) for xy in zip(final_bb.longitude,final_bb.latitude)]
add_gdf = gpd.GeoDataFrame(final_bb, geometry=geometry)

In [23]:
#Create and plot map
import folium
gjson_adds = add_gdf['geometry'].to_json()

#NYC Lat/long, and min and max points
nyc_coords = [40.730610, -73.935242]
borders = {'min_latitude':final_bb['latitude'].min(),'max_latitude':final_bb['latitude'].max(),'min_longitude':final_bb['longitude'].min(),'max_longitude':final_bb['longitude'].max()}
#Create the map
map = folium.Map(location = nyc_coords, zoom_start = 11,control_scale=True,tiles='cartodbpositron',width='100%', height='100%')

#Plot points on map
adds = folium.features.GeoJson(gjson_adds)
map.add_child(adds)

In [40]:
points = list(zip(add_gdf.longitude,add_gdf.latitude,add_gdf.Restaurant,add_gdf.Neighborhood,add_gdf.Borough,add_gdf.Address,add_gdf.Service,add_gdf.Phone,add_gdf.Website,add_gdf.Merch,add_gdf.Gift_Cards))
for point in points:         
      popup_text = "Restaurant : {Restaurant}, Neighborhood: {Neighborhood}, Address: {Address}".format(Restaurant = point[2], Neighborhood = point[3], Address = point[5])
      popup = folium.Popup(popup_text, autopan='False', parse_html=True)    
      marker = folium.Marker(location=[point[1], point[0]], 
                                   popup=popup, 
                                   icon = folium.Icon(icon_size=(25, 25), color = 'orange', icon='motorcycle', prefix='fa')).add_to(map)
map